In [ ]:
# TODO: doctest this .ipynb with pytest.

# Introduction

With `trading-gym` you can:
1. Create custom trading environments (e.g. custom features, reward, assets)
2. Use previously created environments from the registry.

In this notebook we will solve a previously created environment with ray.

# Playground

## Instance the environment

Load the environment `GAIAPredictorsContinuousV7`, which is the latest version of what Aric wanted me to solve.

In [3]:
import trading_gym
from trading_gym.registry.gaia.v7.env import GAIAPredictorsContinuousV7
from datetime import datetime
from collections import namedtuple
import json
import os
import pandas as pd
import ray
print(datetime.now())
print(trading_gym.__name__, trading_gym.__version__)
print(ray.__name__, ray.__version__)

2019-08-20 22:29:02.287199
trading_gym 0.8.1
ray 0.7.3


`ray` requires all custom environments (such as the ones which can be created with `trading-gym`) to accept the optional argument `env_config` in their initialization (e.g. see [this example](https://github.com/ray-project/ray/blob/master/python/ray/rllib/examples/custom_env.py) or [read the docs](https://ray.readthedocs.io/en/latest/rllib-env.html#rllib-environments)). `env_config` allows to pass optional custom configurations to the custom environment.

In our case, we want to split all data the env in two folds: in-sample and out-of-sample.

In [4]:
env_config = dict()
env_config['folds'] =  {
    'training-set': [datetime.min, datetime(2008, 3, 18)],
    'test-set': [datetime(2008, 3, 19), datetime.max],
}
env = GAIAPredictorsContinuousV7(env_config)
env

## Observation space

The observation space (state) is a vector of 3 real numbers (this can be customized):
1. GAIA predictor for Russell 1000
2. GAIA predictor for Russell 1000 - previous GAIA predictor
3. Dummy variable indicating if GAIA predictor for Russell 1000 is zero (i.e. not available).

In [5]:
env.observation_space

Box(3,)

## Action space

Simplex is ray's action space associated with the Dirichlet distribution ([reference](https://github.com/ray-project/ray/issues/4440))

Note that Dirichlet (Simplex) is 2-dimensional but there are 3 contracts. In this particular environment, `Cash` is always assumed to be 0% (design choice), so the agent does not get a choice on the target amount of cash in the portfolio.

In [4]:
env.action_space

Simplex((2,); [1, 1])

In [5]:
env.action_space.contracts

[Cash(USD), ETF(Russell 1000, SMART, USD), ETF(7-10Y T-Bills, SMART, USD)]

In [6]:
env.action_space.sample()

array([0.9516352 , 0.04836483], dtype=float32)

## Interact with the environment
Interact with the environment until when the episode has finished. This API is 100% the same as the one implemented in `openai-gym`, so if you are not familiar with it please [read the docs](https://gym.openai.com/docs/).

At each step (associated with the timestamp `env.now`), the agent uses the state $\mathbf{s} \in \mathbb{R}^3$ to take the action $\mathbf{a} \in \mathbb{R}^3$ subject to $\sum_{i=1}^{n=3} a_i=1$ representing the target weight of the portfolio. If the target weights differ from the current weights, then there will be a rebalancing of the portfolio, meaning that assets will be sold/bought in order to bring the current weight to the target level. The reward $r \in \mathbb{R}$ indicates the simple percentage change in the net liquidation value in dollars of the agent.

In [8]:
Interaction = namedtuple('Interaction', ['time', 's', 'a', 'r', "s_prime"])

state = env.reset()  # 'training-set' by default
done = False
while not done:
    old_state = state
    action = env.action_space.sample()
    state, reward, done, info = env.step(action)
    
    # This print should show that something is going on.
    print(Interaction(env.now, old_state, action, reward, state), '\n')

print('End of the episode, you are done.')

Interaction(time=Timestamp('2007-09-03 00:00:00'), s=array([ 1.2695895 ,  2.67764494, -1.        ]), a=array([0.5274689, 0.4725311], dtype=float32), r=5.946156874547803e-05, s_prime=array([ 1.86227179,  1.2500046 , -1.        ])) 

Interaction(time=Timestamp('2007-09-04 00:00:00'), s=array([ 1.86227179,  1.2500046 , -1.        ]), a=array([0.560311, 0.439689], dtype=float32), r=0.005561203789692604, s_prime=array([ 2.2995324 ,  0.92221043, -1.        ])) 

Interaction(time=Timestamp('2007-09-05 00:00:00'), s=array([ 2.2995324 ,  0.92221043, -1.        ]), a=array([0.7738601 , 0.22613987], dtype=float32), r=-0.0065893325685768556, s_prime=array([ 2.12572615, -0.36656843, -1.        ])) 

Interaction(time=Timestamp('2007-09-06 00:00:00'), s=array([ 2.12572615, -0.36656843, -1.        ]), a=array([0.5096948, 0.4903052], dtype=float32), r=0.0011510323569501324, s_prime=array([ 1.95916477, -0.35128853, -1.        ])) 

Interaction(time=Timestamp('2007-09-07 00:00:00'), s=array([ 1.95916477,

## Visualizations
All visualizations already implemented in `trading-gym` for you can be found in `Renderer`. From this class, you can produce visualizations (using the method `.to_plotly`) or retrieve the underlying data (`.to_frame`).

In [9]:
renderer = env.render()
renderer

In [10]:
# renderer's methods. 
list(vars(renderer).keys())

['track_record',
 'benchmark',
 'risk_free',
 'cost_of_commissions',
 'cost_of_spread',
 'target_weights',
 'pnl',
 'performance_contribution',
 'risk_contribution',
 'cumulative_performance',
 'level',
 'capm']

We now visualize a few stuffs:
1. `target_weights`: historical actions
2. `pnl`: (cumulative) profit and losses through time.
3. `cumulative_performance`:  (cumulative) profit and losses through time as a percentage of the starting capital ($100 by default)

In [11]:
renderer.target_weights.to_plotly()
renderer.pnl.to_plotly()
renderer.cumulative_performance.to_plotly()

## Tearsheet
Common financial metrics to assess return, risk, and risk-adjusted return of an investment. These numbers are incredibly useful when displayed in `tensorboard` over the number of training iterations.

We can (optionally) a few optional argument to `tearsheet` in enrich the number of metrics returned.

Description and source code for these metrics can be found in `trading_gym.metrics` or just google them.

In [12]:
levels = renderer.level.to_frame()
levels.tearsheet(
    risk_free=env._load_risk_free(),
    benchmark=env._load_benchmark(),
    weights=renderer.track_record.to_frame('weights_target'),
)

Strategy  \
Context              From                                       2007-08-31   
                     To                                         2007-09-27   
                     Years                                       0.0739726   
                     Observations                                       20   
                     Risk-free asset                 Index(USD 1M Deposit)   
                     Risk-free CAGR                              0.0572772   
Return               CAGR                                         0.476049   
                     CAGR over cash                               0.418771   
                     Overall return                              0.0292214   
Risk                 Volatility                                  0.0756612   
                     Downside volatility                         0.0668255   
                     Upside volatility                           0.0466685   
                     Max drawdown                               -0.0104584   
                     Martin risk                                0.00426707   
                     VaR 5%                                    -0.00697624   
                     VaR 2%                                    -0.00906552   
                     Expected shortfall 5%                      -0.0104584   
                     Expected shortfall 2%                      -0.0104584   
Risk-adjusted return Sharpe ratio                                  5.53482   
                     Sortino ratio                                 6.26664   
                     Calmar ratio                                  40.0417   
                     Martin ratio                                  98.1402   
Outperformance       Benchmark name                  Index(Aric-Benchmark)   
                     CAGR over benchmark                           -0.2482   
                     Information ratio                            -1.72719   
                     CAPM Alpha                                   0.264017   
                     CAPM Beta                                    0.195123   
Weights              Cash(USD)                                           0   
                     ETF(Russell 1000, SMART, USD)                0.481471   
                     ETF(7-10Y T-Bills, SMART, USD)               0.518529   
                     Leverage mean                                       1   
                     Turnover daily                               0.647165   
                     Turnover annual                               163.085   

                                                     Index(Aric-Benchmark)  \
Context              From                                       2007-08-31   
                     To                                         2007-09-27   
                     Years                                       0.0739726   
                     Observations                                       20   
                     Risk-free asset                 Index(USD 1M Deposit)   
                     Risk-free CAGR                              0.0572772   
Return               CAGR                                         0.724249   
                     CAGR over cash                               0.666972   
                     Overall return                              0.0411227   
Risk                 Volatility                                   0.155471   
                     Downside volatility                         0.0875105   
                     Upside volatility                            0.125771   
                     Max drawdown                               -0.0248472   
                     Martin risk                                0.00946788   
                     VaR 5%                                      -0.011199   
                     VaR 2%                                     -0.0144724   
                     Expected shortfall 5%                      -0.0166546   
         

## Out of sample assessment of a (random) agent
The ONLY difference is to specify the 'test-set' when resetting the environment ('training-set' by default). So here I'm just copy-pasting the code that we previously used to interact with the environment.

In practice, the action should now be a random action but an output of your policy network, and you want the results ('Strategy') to look as good as possible out-of-sample. If the strategy is as good as Aric's benchmark, then the RL solution might be deployed in production.

In [13]:
# Interact with the environment.
state = env.reset(fold='test-set')  # 'training-set' by default
done = False
while not done:
    action = env.action_space.sample()
    state, reward, done, info = env.step(action)
    
# Render results (your (random) agent is labelled as 'Strategy').
renderer = env.render()
renderer.plotly_report()
renderer.tearsheet()

Strategy  \
Context              From                                       2008-03-19   
                     To                                         2018-08-28   
                     Years                                         10.4493   
                     Observations                                     2725   
                     Risk-free asset                 Index(USD 1M Deposit)   
                     Risk-free CAGR                             0.00681294   
Return               CAGR                                         0.104861   
                     CAGR over cash                              0.0980485   
                     Overall return                                1.83489   
Risk                 Volatility                                   0.086638   
                     Downside volatility                         0.0658178   
                     Upside volatility                           0.0621241   
                     Max drawdown                                -0.118014   
                     Martin risk                                 0.0309363   
                     VaR 5%                                    -0.00821286   
                     VaR 2%                                     -0.0122285   
                     Expected shortfall 5%                      -0.0127868   
                     Expected shortfall 2%                      -0.0171716   
Risk-adjusted return Sharpe ratio                                   1.1317   
                     Sortino ratio                                  1.4897   
                     Calmar ratio                                 0.830824   
                     Martin ratio                                  3.16937   
Outperformance       Benchmark name                  Index(Aric-Benchmark)   
                     CAGR over benchmark                        -0.0537242   
                     Information ratio                           -0.733599   
                     CAPM Alpha                                  0.0074141   
                     CAPM Beta                                    0.613739   
Weights              Cash(USD)                                           0   
                     ETF(Russell 1000, SMART, USD)                 0.40096   
                     ETF(7-10Y T-Bills, SMART, USD)                0.59904   
                     Leverage mean                                       1   
                     Turnover daily                               0.542066   
                     Turnover annual                               136.601   

                                                     Index(Aric-Benchmark)  \
Context              From                                       2008-03-19   
                     To                                         2018-08-28   
                     Years                                         10.4493   
                     Observations                                     2725   
                     Risk-free asset                 Index(USD 1M Deposit)   
                     Risk-free CAGR                             0.00681294   
Return               CAGR                                         0.158586   
                     CAGR over cash                               0.151773   
                     Overall return                                3.65592   
Risk                 Volatility                                  0.0970738   
                     Downside volatility                          0.069906   
                     Upside volatility                           0.0705399   
                     Max drawdown                               -0.0865477   
                     Martin risk                                 0.0189993   
                     VaR 5%                                    -0.00895352   
                     VaR 2%                                     -0.0134313   
                     Expected shortfall 5%                      -0.0137858   
         

# Solve GAIA-v7 with ray (2-folds split)

In [6]:
import ray
from ray import rllib, tune
from trading_gym.ray.logger import calculate_tearsheet, CustomLogger
from copy import deepcopy
ray.init()
ray.__version__

2019-06-21 16:20:32,454	WARNING worker.py:1331 -- WARNING: Not updating worker name since `setproctitle` is not installed. Install this with `pip install setproctitle` (or ray[debug]) to enable monitoring of worker processes.
2019-06-21 16:20:32,466	INFO node.py:498 -- Process STDOUT and STDERR is being redirected to /tmp/ray/session_2019-06-21_16-20-32_465718_36057/logs.
2019-06-21 16:20:32,609	INFO services.py:409 -- Waiting for redis server at 127.0.0.1:23371 to respond...
2019-06-21 16:20:32,749	INFO services.py:409 -- Waiting for redis server at 127.0.0.1:19700 to respond...
2019-06-21 16:20:32,755	INFO services.py:806 -- Starting Redis shard with 10.0 GB max memory.
2019-06-21 16:20:32,834	INFO node.py:512 -- Process STDOUT and STDERR is being redirected to /tmp/ray/session_2019-06-21_16-20-32_465718_36057/logs.
2019-06-21 16:20:32,837	WARNING services.py:1294 -- Warning: Capping object memory store to 20.0GB. To increase this further, specify `object_store_memory` when calling r

'0.7.1'

## Setting up the experiment

In [17]:
config = rllib.agents.ppo.DEFAULT_CONFIG.copy()
config['env'] = GAIAPredictorsContinuousV7
config['gamma'] = tune.grid_search([0])
config['num_workers'] = 6
config['callbacks']['on_train_result'] = tune.function(calculate_tearsheet)
config['entropy_coeff'] = tune.grid_search([1e-5])
config['batch_mode'] = 'complete_episodes'
config['use_lstm']: False
config['lr'] = tune.grid_search([1e-5])
config['num_sgd_iter'] = tune.grid_search([8])
config['sgd_minibatch_size'] = 128
config['train_batch_size'] = tune.grid_search([4000])
config['use_gae'] = tune.grid_search([False])
config['vf_share_layers'] = False
config['vf_loss_coeff'] = tune.grid_search([0.])
config['vf_clip_param'] = tune.grid_search([0.])
config['lambda'] = tune.grid_search([0.])
config['kl_coeff'] = 0.2
config['kl_target'] = 0.01
config['clip_param'] = 0.55

Note that we pass the previously defined `env_config` here, which will be used internally by `ray` to initialize the env(s).

In [18]:
config['env_config'] = env_config

In [29]:
experiment = tune.Experiment(
    name='Playground-2folds',
    run=rllib.agents.ppo.PPOTrainer,
    stop={"timesteps_total": 1000000},
    config=deepcopy(config),
    num_samples=1,
    local_dir='logs',
    #checkpoint_freq=int(1e4 / config['train_batch_size']),  # checkpoint every 100k iters
    checkpoint_at_end=True,
    max_failures=0,
    loggers=[CustomLogger],
)

## Custom network architecture (OPTIONAL)
The default architecture in `ray` in a MLP with 2-layers, 256 units per layer with tanh. As an exercise, say that we want to use dropout. In order to do that, we create a [custom architecture](https://ray.readthedocs.io/en/latest/rllib-models.html#custom-models-tensorflow).

TODO: make sure that dropout is handled correctly at test time.

In [15]:
from ray.rllib.models import ModelCatalog
from ray.rllib.models.model import Model
from ray.rllib.models.misc import normc_initializer, get_activation_fn
import tensorflow as tf
import tensorflow.contrib.slim as slim


class MLP(Model):
    def _build_layers_v2(self, input_dict: dict, num_outputs: int, config: dict):
        import tensorflow.contrib.slim as slim

        with tf.name_scope("fc_net"):
            last_layer = input_dict['obs']
            activation = get_activation_fn(config.get("fcnet_activation"))
            for i, size in enumerate(config.get("fcnet_hiddens"), 1):
                last_layer = slim.fully_connected(
                    inputs=last_layer,
                    num_outputs=size,
                    weights_initializer=normc_initializer(1.0),
                    activation_fn=activation,
                    scope="fc{}".format(i),
                )
                last_layer = tf.layers.dropout(
                    inputs=last_layer,
                    rate=config['custom_options']["fcnet_dropout_rate"],
                    training=input_dict['is_training'],
                    name="dropout{}".format(i),
                )
            output = slim.fully_connected(
                inputs=last_layer,
                num_outputs=num_outputs,
                weights_initializer=normc_initializer(0.01),
                activation_fn=None,
                scope="fc_out",
            )
            return output, last_layer

ModelCatalog.register_custom_model(MLP.__name__, MLP)

In [19]:
config['model']['custom_options'] = {'fcnet_dropout_rate': 0.5}
config['model']['custom_model'] = MLP.__name__

## Run the experiment
Results are automatically saved to disk. Later on, we will restore an agent that we trained in this section.

NTN: Saves to both the local directory 'logs' and 'ray_results's

In [ ]:
trials = tune.run_experiments(
    experiments=experiment,
    search_alg=tune.suggest.BasicVariantGenerator(),
    scheduler=tune.schedulers.FIFOScheduler(),
    verbose=1,
    reuse_actors=False,
    resume=False,
)

## Tensorboard
Tensorboard

![alt text](tensorboard-playground-2-folds.png "Title")

## Restore the agent
All objects saved to disk by `ray` must be serialized (~pickled). This does not seem very clean, but I've not found a better way to restore agents so far. Please do explore alternative or raise an issue in ray and ask.

In [2]:
from ray import cloudpickle
from ray.utils import binary_to_hex, hex_to_binary


def cloudpickleloads(obj):
    if isinstance(obj, dict):
        try:
            return cloudpickle.loads(hex_to_binary(obj["value"]))
        except:
            for key, value in obj.items():
                if isinstance(value, dict):
                    if sorted(value) == ['_type', 'value']:
                        obj[key] = cloudpickle.loads(hex_to_binary(value["value"]))
                    else:
                        obj[key] = cloudpickleloads(value)
                elif isinstance(value, list):
                    for i, item in enumerate(value):
                        obj[key][i] = cloudpickleloads(item)
    return obj

In [12]:
path = '/home/Nicholas/Desktop/trading-gym/logs/Playground-2folds/experiment_state-2019-06-17_10-01-21.json'
# path = '/home/Nicholas/Desktop/trading-gym/notebooks/registry/gaia/v7/logs/Playground-2folds-tuning/experiment_state-2019-06-20_15-53-36.json'
# path = '/home/Nicholas/Desktop/trading-gym/notebooks/registry/gaia/v7/logs/Playground-2folds-tuning/experiment_state-2019-06-20_15-53-36.json'

with open(path) as f:
    metadata = json.load(f)

runner_data = metadata['runner_data']
stats = metadata['stats']

checkpoint = metadata['checkpoints'][-1]
checkpoint = cloudpickleloads(checkpoint)
checkpoint_path = cloudpickle.loads(hex_to_binary(checkpoint['_checkpoint'])).value
print(checkpoint_path)

config = checkpoint['config']
env_cls = config['env']
env_config = config['env_config']
path_restore = os.path.join(checkpoint['logdir'], checkpoint_path)

logs/Playground-2folds/PPOTrainer_GAIAPredictorsContinuousV7_0_entropy_coeff=1e-05,gamma=0,lambda=0.0,lr=1e-05,num_sgd_iter=8,train_batch_size=4000,use_g_2019-06-17_10-01-21ymqkrkjb/checkpoint_250/checkpoint-250


In [13]:
agent = rllib.agents.ppo.PPOTrainer(config, env_cls)
agent.restore(path_restore)

2019-06-21 16:29:10,891	WARNING ppo.py:153 -- FYI: By default, the value function will not share layers with the policy model ('vf_share_layers': False).
2019-06-21 16:29:12,613	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 0 on CPU (please ignore any CUDA init errors)


<class 'module'>


2019-06-21 16:29:14,786	INFO policy_evaluator.py:735 -- Built policy map: {'default_policy': <ray.rllib.policy.tf_policy_template.PPOTFPolicy object at 0x7f3164671be0>}
2019-06-21 16:29:14,789	INFO policy_evaluator.py:736 -- Built preprocessor map: {'default_policy': <ray.rllib.models.preprocessors.NoPreprocessor object at 0x7f3164671898>}
2019-06-21 16:29:14,791	INFO policy_evaluator.py:347 -- Built filter map: {'default_policy': <ray.rllib.utils.filter.NoFilter object at 0x7f31646713c8>}
2019-06-21 16:29:15,004	INFO multi_gpu_optimizer.py:80 -- LocalMultiGPUOptimizer devices ['/cpu:0']


NameError: name 'path_restore' is not defined

## Run and visualize the agent out-of-sample
`.sample_episode` allows to easily assess an agent on a specific fold of the data. All parameters are optional and they default to testing a random agent on the training-set. Episode should collect most of the information (if not all) needed to assess the results of a policy in a given fold.

In [ ]:
episode = env.sample_episode(
    fold='test-set',
    policy=agent,
    episode_length=None,
    benchmark=env._load_benchmark().squeeze(),
    risk_free=env._load_risk_free().squeeze(),
    burn=1,
)

In [ ]:
episode.renderer.plotly_report()
episode.renderer.tearsheet()

(pid=37006) 2019-06-21 16:29:24,434	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 1 on CPU (please ignore any CUDA init errors)
(pid=37006) <class 'module'>
(pid=37006) 2019-06-21 16:29:24.474987: I tensorflow/core/platform/cpu_feature_guard.cc:141] Your CPU supports instructions that this TensorFlow binary was not compiled to use: SSE4.1 SSE4.2 AVX AVX2 FMA
(pid=37005) 2019-06-21 16:29:24,641	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 2 on CPU (please ignore any CUDA init errors)
(pid=37005) <class 'module'>
(pid=37005) 2019-06-21 16:29:24.697700: I tensorflow/core/platform/cpu_feature_guard.cc:141] Your CPU supports instructions that this TensorFlow binary was not compiled to use: SSE4.1 SSE4.2 AVX AVX2 FMA
(pid=37006) 2019-06-21 16:29:25,319	INFO dynamic_tf_policy.py:265 -- Initializing loss function with dummy input:
(pid=37006) 
(pid=37006) { 'action_prob': <tf.Tensor 'default_policy/action_prob:0' shape=(?,) dtype=float32>,
(pid=37006)  

Now we use `episode` is create a couple of charts which help to understand/visualize the  behavior of the RL agent.

In [22]:
from trading_gym.contracts import ETF, Index


# Load.
actions = episode.actions_as_frame()
states = episode.states_as_frame()

# Parse.
gaia_predictor = states[0].to_frame('GAIA Predictor')
target_weight_russell_1000 = actions[ETF('Russell 1000')]
target_weight_russell_1000.name = 'Target weight: ' + str(target_weight_russell_1000.name)
mapping = gaia_predictor.join(target_weight_russell_1000)

# Visualize.
mapping.iplot(
    title="Hisorical GAIA predictor for Russell 1000 vs agent's target weights",
    secondary_y='GAIA Predictor',
    yTitle=target_weight_russell_1000.name,
    secondary_y_title='GAIA Predictor',
    legend={'orientation': 'h'},
)
mapping.set_index('GAIA Predictor').iplot(
    title='Policy: mapping from GAIA predictor (state) to target weight for Russell 1000 (action)',
    xTitle='GAIA predictor for Russell 1000 (standardized)',
    yTitle='Target weight for Russell 1000',
    kind='scatter',
    mode='markers',
    size=4,
)

## Conclusions

As we can see from the tearsheet and chart above, the RL agent does not outperform the benchmark out-of-sample. Visualizing the mapping functions allows to know in advance how the RL agent would behave in previously unseen situations and its a nice visualization to communicate results and trust the results.

Walk-forward optimization is certainly something sensible to try as this naive 2-folds split assumes not re-training of the RL agent during the out-of-sample period as new data arrive. In the next section we repeat the same process while re-training the RL agent every year.

# Solve GAIA-v7 with ray (walk-forward, no transfer learning)
TODO

## Set up and run the experiment(s)

In [20]:
for year in range(2007, 2018):
    print('_______________________________________{}____________________________________________'.format(year))
    config['env_config'] = {
        'folds': {
            'training-set': [datetime.min, datetime(year, 12, 31)],
            'test-set': [datetime(year + 1, 1, 1), datetime(year + 1, 12, 31)],
        }
    }
    experiment = tune.Experiment(
        name='Playground-WalkForward{}'.format(year),
        run=rllib.agents.ppo.PPOTrainer,
        stop={"timesteps_total": 50000},
        config=deepcopy(config),
        num_samples=1,
        local_dir='logs',
        #checkpoint_freq=int(1e4 / config['train_batch_size']),  # checkpoint every 100k iters
        checkpoint_at_end=True,
        max_failures=0,
        loggers=[CustomLogger],
    )
    trials = tune.run_experiments(
        experiments=experiment,
        search_alg=tune.suggest.BasicVariantGenerator(),
        scheduler=tune.schedulers.FIFOScheduler(),
        verbose=0,
        reuse_actors=False,
        resume=False,
    )

2019-06-17 15:01:34,304	INFO tune.py:65 -- Did not find checkpoint file in logs/Playground-WalkForward2007.
2019-06-17 15:01:34,305	INFO tune.py:232 -- Starting a new experiment.


_______________________________________2007____________________________________________
(pid=96351) 2019-06-17 15:01:38,805	WARNING ppo.py:153 -- FYI: By default, the value function will not share layers with the policy model ('vf_share_layers': False).
(pid=96351) 2019-06-17 15:01:39,538	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 0 on CPU (please ignore any CUDA init errors)
(pid=96351) 2019-06-17 15:01:39.539850: I tensorflow/core/platform/cpu_feature_guard.cc:141] Your CPU supports instructions that this TensorFlow binary was not compiled to use: SSE4.1 SSE4.2 AVX AVX2 FMA
(pid=96351) <class 'module'>
(pid=96351) 2019-06-17 15:01:47,225	INFO dynamic_tf_policy.py:265 -- Initializing loss function with dummy input:
(pid=96351) 
(pid=96351) { 'action_prob': <tf.Tensor 'default_policy/action_prob:0' shape=(?,) dtype=float32>,
(pid=96351)   'actions': <tf.Tensor 'default_policy/actions:0' shape=(?, 2) dtype=float32>,
(pid=96351)   'advantages': <tf.Tensor 'default_

(pid=96355) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=96355) 
(pid=96355) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=96355) 
(pid=96353) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=96353) 
(pid=96353) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=96353) 
(pid=96352) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=96352) 
(pid=96352) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=96352) 
(pid=96348) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=96348) 
(pid=96348) Converting sparse IndexedSlices to a

(pid=96351) 2019-06-17 15:03:27,843	INFO multi_gpu_impl.py:146 -- Training on concatenated sample batches:
(pid=96351) 
(pid=96351) { 'inputs': [ np.ndarray((4000, 2), dtype=float32, min=0.0, max=1.0, mean=0.475),
(pid=96351)               np.ndarray((4000,), dtype=float32, min=-0.027, max=0.028, mean=0.0),
(pid=96351)               np.ndarray((4000, 3), dtype=float32, min=-14.063, max=11.025, mean=0.09),
(pid=96351)               np.ndarray((4000, 2), dtype=float32, min=0.0, max=1.0, mean=0.5),
(pid=96351)               np.ndarray((4000,), dtype=float32, min=-6.374, max=6.426, mean=-0.0),
(pid=96351)               np.ndarray((4000, 2), dtype=float32, min=-0.016, max=0.016, mean=0.002),
(pid=96351)               np.ndarray((4000,), dtype=float32, min=0.0, max=0.0, mean=0.0),
(pid=96351)               np.ndarray((4000,), dtype=float32, min=0.0, max=0.0, mean=0.0)],
(pid=96351)   'placeholders': [ <tf.Tensor 'default_policy/action:0' shape=(?, 2) dtype=float32>,
(pid=96351)              

2019-06-17 15:07:20,622	INFO ray_trial_executor.py:187 -- Destroying actor for trial PPOTrainer_GAIAPredictorsContinuousV7_0_entropy_coeff=1e-05,gamma=0,lambda=0.0,lr=1e-05,num_sgd_iter=8,train_batch_size=4000,use_gae=False,vf_clip_param=0.0,vf_loss_coeff=0.0. If your trainable is slow to initialize, consider setting reuse_actors=True to reduce actor creation overheads.
2019-06-17 15:07:20,649	INFO tune.py:65 -- Did not find checkpoint file in logs/Playground-WalkForward2008.
2019-06-17 15:07:20,650	INFO tune.py:232 -- Starting a new experiment.


...

2019-06-17 15:59:24,362	INFO ray_trial_executor.py:187 -- Destroying actor for trial PPOTrainer_GAIAPredictorsContinuousV7_0_entropy_coeff=1e-05,gamma=0,lambda=0.0,lr=1e-05,num_sgd_iter=8,train_batch_size=4000,use_gae=False,vf_clip_param=0.0,vf_loss_coeff=0.0. If your trainable is slow to initialize, consider setting reuse_actors=True to reduce actor creation overheads.
2019-06-17 15:59:24,386	INFO tune.py:65 -- Did not find checkpoint file in logs/Playground-WalkForward2017.
2019-06-17 15:59:24,386	INFO tune.py:232 -- Starting a new experiment.


_______________________________________2017____________________________________________
(pid=60096) 2019-06-17 15:59:30,587	WARNING ppo.py:153 -- FYI: By default, the value function will not share layers with the policy model ('vf_share_layers': False).
(pid=60096) 2019-06-17 15:59:31,471	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 0 on CPU (please ignore any CUDA init errors)
(pid=60096) 2019-06-17 15:59:31.471788: I tensorflow/core/platform/cpu_feature_guard.cc:141] Your CPU supports instructions that this TensorFlow binary was not compiled to use: SSE4.1 SSE4.2 AVX AVX2 FMA
(pid=60096) <class 'module'>
(pid=60096) 2019-06-17 15:59:39,486	INFO dynamic_tf_policy.py:265 -- Initializing loss function with dummy input:
(pid=60096) 
(pid=60096) { 'action_prob': <tf.Tensor 'default_policy/action_prob:0' shape=(?,) dtype=float32>,
(pid=60096)   'actions': <tf.Tensor 'default_policy/actions:0' shape=(?, 2) dtype=float32>,
(pid=60096)   'advantages': <tf.Tensor 'default_

(pid=60086) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=60086) 
(pid=60086) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=60086) 
(pid=60084) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=60084) 
(pid=60084) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=60084) 
(pid=60081) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=60081) 
(pid=60081) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=60081) 
(pid=60094) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=60094) 
(pid=60094) Converting sparse IndexedSlices to a

(pid=60096) 2019-06-17 16:01:18,627	INFO multi_gpu_impl.py:146 -- Training on concatenated sample batches:
(pid=60096) 
(pid=60096) { 'inputs': [ np.ndarray((4000, 2), dtype=float32, min=0.0, max=1.0, mean=0.475),
(pid=60096)               np.ndarray((4000,), dtype=float32, min=-0.029, max=0.037, mean=0.0),
(pid=60096)               np.ndarray((4000, 3), dtype=float32, min=-14.063, max=11.937, mean=0.064),
(pid=60096)               np.ndarray((4000, 2), dtype=float32, min=0.0, max=1.0, mean=0.5),
(pid=60096)               np.ndarray((4000,), dtype=float32, min=-6.425, max=8.653, mean=-0.0),
(pid=60096)               np.ndarray((4000, 2), dtype=float32, min=-0.011, max=0.004, mean=-0.004),
(pid=60096)               np.ndarray((4000,), dtype=float32, min=0.0, max=0.0, mean=0.0),
(pid=60096)               np.ndarray((4000,), dtype=float32, min=0.0, max=0.0, mean=0.0)],
(pid=60096)   'placeholders': [ <tf.Tensor 'default_policy/action:0' shape=(?, 2) dtype=float32>,
(pid=60096)            

2019-06-17 16:05:01,312	INFO ray_trial_executor.py:187 -- Destroying actor for trial PPOTrainer_GAIAPredictorsContinuousV7_0_entropy_coeff=1e-05,gamma=0,lambda=0.0,lr=1e-05,num_sgd_iter=8,train_batch_size=4000,use_gae=False,vf_clip_param=0.0,vf_loss_coeff=0.0. If your trainable is slow to initialize, consider setting reuse_actors=True to reduce actor creation overheads.


In [71]:
# raise ValueError('TODO: update paths with latest runs')
paths = {2007: '/home/Nicholas/Desktop/trading-gym/notebooks/registry/gaia/v7/logs/Playground-WalkForward2007/experiment_state-2019-06-17_15-01-34.json',
        2008: '/home/Nicholas/Desktop/trading-gym/notebooks/registry/gaia/v7/logs/Playground-WalkForward2008/experiment_state-2019-06-17_15-07-20.json',
        2009: '/home/Nicholas/Desktop/trading-gym/notebooks/registry/gaia/v7/logs/Playground-WalkForward2009/experiment_state-2019-06-17_15-13-08.json',
        2010: '/home/Nicholas/Desktop/trading-gym/notebooks/registry/gaia/v7/logs/Playground-WalkForward2010/experiment_state-2019-06-17_15-18-58.json',
        2011: '/home/Nicholas/Desktop/trading-gym/notebooks/registry/gaia/v7/logs/Playground-WalkForward2011/experiment_state-2019-06-17_15-24-51.json',
        2012: '/home/Nicholas/Desktop/trading-gym/notebooks/registry/gaia/v7/logs/Playground-WalkForward2012/experiment_state-2019-06-17_15-30-36.json',
        2013: '/home/Nicholas/Desktop/trading-gym/notebooks/registry/gaia/v7/logs/Playground-WalkForward2013/experiment_state-2019-06-17_15-36-24.json',
        2014: '/home/Nicholas/Desktop/trading-gym/notebooks/registry/gaia/v7/logs/Playground-WalkForward2014/experiment_state-2019-06-17_15-42-09.json',
        2015: '/home/Nicholas/Desktop/trading-gym/notebooks/registry/gaia/v7/logs/Playground-WalkForward2015/experiment_state-2019-06-17_15-47-54.json',
        2016: '/home/Nicholas/Desktop/trading-gym/notebooks/registry/gaia/v7/logs/Playground-WalkForward2016/experiment_state-2019-06-17_15-53-39.json',
        2017: '/home/Nicholas/Desktop/trading-gym/notebooks/registry/gaia/v7/logs/Playground-WalkForward2017/experiment_state-2019-06-17_15-59-24.json'
        }


episodes = dict()
agents = dict()
for year, path in paths.items():
    # RESTORE part (a)
    with open(path) as f:
        metadata = json.load(f)

    runner_data = metadata['runner_data']
    stats = metadata['stats']

    checkpoint = metadata['checkpoints'][-1]
    checkpoint = cloudpickleloads(checkpoint)
    checkpoint_path = cloudpickle.loads(hex_to_binary(checkpoint['_checkpoint'])).value

    config = checkpoint['config']
#     Don't actually need to redefine the env_cls as it's always the same 
    env_cls = config['env']
    env_config = config['env_config']
    path_restore = os.path.join(checkpoint['logdir'], checkpoint_path)
    
    # RESTORE part (b)
    agent = rllib.agents.ppo.PPOTrainer(config, env_cls)
#     agent.restore(path_restore)
# THIS IS A BUG: 
    agent._restore(path_restore)
    
    env = env_cls(env_config)
    episode = env.sample_episode(
        fold='test-set',
        policy=agent,
        episode_length=None,
        benchmark=env._load_benchmark().squeeze(),
        risk_free=env._load_risk_free().squeeze(),
        burn=1,
    )
    
    episodes[year] = episode
    agents[year] = agent

2019-06-18 16:09:23,290	WARNING ppo.py:153 -- FYI: By default, the value function will not share layers with the policy model ('vf_share_layers': False).
2019-06-18 16:09:24,784	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 0 on CPU (please ignore any CUDA init errors)


<class 'module'>


2019-06-18 16:09:33,837	INFO policy_evaluator.py:735 -- Built policy map: {'default_policy': <ray.rllib.policy.tf_policy_template.PPOTFPolicy object at 0x7fb99f649f98>}
2019-06-18 16:09:33,839	INFO policy_evaluator.py:736 -- Built preprocessor map: {'default_policy': <ray.rllib.models.preprocessors.NoPreprocessor object at 0x7fb99f649b70>}
2019-06-18 16:09:33,840	INFO policy_evaluator.py:347 -- Built filter map: {'default_policy': <ray.rllib.utils.filter.NoFilter object at 0x7fb99f6499b0>}
2019-06-18 16:09:34,253	INFO multi_gpu_optimizer.py:80 -- LocalMultiGPUOptimizer devices ['/cpu:0']
2019-06-18 16:09:48,504	WARNING ppo.py:153 -- FYI: By default, the value function will not share layers with the policy model ('vf_share_layers': False).
2019-06-18 16:09:49,521	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 0 on CPU (please ignore any CUDA init errors)


<class 'module'>


2019-06-18 16:09:51,216	INFO policy_evaluator.py:735 -- Built policy map: {'default_policy': <ray.rllib.policy.tf_policy_template.PPOTFPolicy object at 0x7fb9ca1a4198>}
2019-06-18 16:09:51,216	INFO policy_evaluator.py:736 -- Built preprocessor map: {'default_policy': <ray.rllib.models.preprocessors.NoPreprocessor object at 0x7fb9d02f2d30>}
2019-06-18 16:09:51,217	INFO policy_evaluator.py:347 -- Built filter map: {'default_policy': <ray.rllib.utils.filter.NoFilter object at 0x7fb9ca608f98>}
2019-06-18 16:09:51,330	INFO multi_gpu_optimizer.py:80 -- LocalMultiGPUOptimizer devices ['/cpu:0']


...

(pid=57329) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=57329) 
(pid=57329) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=57329) 
(pid=57314) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=57314) 
(pid=57314) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=57314) 
(pid=57307) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=57307) 
(pid=57307) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=57307) 
(pid=57309) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=57309) 
(pid=57309) Converting sparse IndexedSlices to a

(pid=61626) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=61626) 
(pid=61626) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=61626) 
(pid=61624) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=61624) 
(pid=61624) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=61624) 
(pid=61664) 2019-06-18 16:23:26,393	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 1 on CPU (please ignore any CUDA init errors)
(pid=61664) <class 'module'>
(pid=61664) 2019-06-18 16:23:26.554723: I tensorflow/core/platform/cpu_feature_guard.cc:141] Your CPU supports instructions that this TensorFlow binary was not compiled to use: SSE4.1 SSE4.2 AVX AVX2 FMA
(pid=61625) <class 'module'>
(pid=61625) 2019-06-18 16:23:29,156	INFO polic

(pid=61658) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=61658) 
(pid=61658) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=61658) 
(pid=61623) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=61623) 
(pid=61623) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=61623) 
(pid=61659) /home/Nicholas/anaconda3/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=61659) 
(pid=61659) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=61659) 
(pid=61666) 2019-06-18 16:25:30,797	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 3 on CPU (please ignore any CUDA init errors)
(pid=61666) <class 'module'>
(pid=61

(pid=69062) 2019-06-18 16:27:35,187	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 5 on CPU (please ignore any CUDA init errors)
(pid=69062) <class 'module'>
(pid=69062) 2019-06-18 16:27:35.402929: I tensorflow/core/platform/cpu_feature_guard.cc:141] Your CPU supports instructions that this TensorFlow binary was not compiled to use: SSE4.1 SSE4.2 AVX AVX2 FMA
(pid=69060) <class 'module'>
(pid=69060) 2019-06-18 16:27:37,825	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 6 on CPU (please ignore any CUDA init errors)
(pid=69060) 2019-06-18 16:27:38.064044: I tensorflow/core/platform/cpu_feature_guard.cc:141] Your CPU supports instructions that this TensorFlow binary was not compiled to use: SSE4.1 SSE4.2 AVX AVX2 FMA
(pid=69086) <class 'module'>
(pid=69086) 2019-06-18 16:27:40,209	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 1 on CPU (please ignore any CUDA init errors)
(pid=69086) 2019-06-18 16:27:40.456829: I tensorflow/core/pla

(pid=73193) 2019-06-18 16:31:28,314	INFO dynamic_tf_policy.py:265 -- Initializing loss function with dummy input:
(pid=73193) 
(pid=73193) { 'action_prob': <tf.Tensor 'default_policy/action_prob:0' shape=(?,) dtype=float32>,
(pid=73193)   'actions': <tf.Tensor 'default_policy/actions:0' shape=(?, 2) dtype=float32>,
(pid=73193)   'advantages': <tf.Tensor 'default_policy/advantages:0' shape=(?,) dtype=float32>,
(pid=73193)   'behaviour_logits': <tf.Tensor 'default_policy/behaviour_logits:0' shape=(?, 2) dtype=float32>,
(pid=73193)   'dones': <tf.Tensor 'default_policy/dones:0' shape=(?,) dtype=bool>,
(pid=73193)   'new_obs': <tf.Tensor 'default_policy/new_obs:0' shape=(?, 3) dtype=float32>,
(pid=73193)   'obs': <tf.Tensor 'default_policy/observation:0' shape=(?, 3) dtype=float32>,
(pid=73193)   'prev_actions': <tf.Tensor 'default_policy/action:0' shape=(?, 2) dtype=float32>,
(pid=73193)   'prev_rewards': <tf.Tensor 'default_policy/prev_reward:0' shape=(?,) dtype=float32>,
(pid=73193)   '

In [51]:
levels = list()
mappings = pd.DataFrame()
mapping_functions = dict()
for year in paths:
    episode = episodes[year]
    agent = agents[year]

    # Load.
    actions = episode.actions_as_frame()
    states = episode.states_as_frame()
    
    # Parse.
    gaia_predictor = states[0].to_frame('GAIA Predictor')
    
#     The following line was here before
#     target_weight_russell_1000 = actions[ETF('Russell 1000')]
    target_weight_russell_1000 = actions[actions.columns[0]]
    target_weight_russell_1000.name = 'Target weight: ' + str(target_weight_russell_1000.name)
    mapping = gaia_predictor.join(target_weight_russell_1000)
    mapping_function = mapping.set_index('GAIA Predictor')

    levels.append(episode.renderer.level.to_frame().pct_change())
    mappings = mappings.append(mapping)
    mapping_functions[year] = mapping_function

    # Visualize.
    mapping.iplot(
        title="Hisorical GAIA predictor for Russell 1000 vs agent's target weights",
        secondary_y='GAIA Predictor',
        yTitle=target_weight_russell_1000.name,
        secondary_y_title='GAIA Predictor',
        legend={'orientation': 'h'},
    )
    mapping_function.iplot(
        title='Policy: mapping from GAIA predictor (state) to target weight for Russell 1000 (action)',
        xTitle='GAIA predictor for Russell 1000 (standardized)',
        yTitle='Target weight for Russell 1000',
        kind='scatter',
        mode='markers',
        size=4,
    )

In [58]:
daily_ret = pd.concat(levels).sort_index().fillna(0)
cumulative_performance = (1 + daily_ret).cumprod() - 1
cumulative_performance *= 100

aric = cumulative_performance.columns[1]
cumulative_performance['Strategy relative to Aric-Benchmark'] = cumulative_performance['Strategy'] - cumulative_performance[aric]


# Visualizations.
cumulative_performance.iplot(
    legend={'orientation': 'h'},
    yTitle='Total returns',
)

In [61]:
levels = (1 + cumulative_performance / 100)
annual_rets = (levels.resample('Y').last() / levels.resample('Y').first() - 1)

    
annual_rets['Strategy relative to Aric-Benchmark'] = annual_rets['Strategy'] - annual_rets[aric]
annual_rets.index = annual_rets.index.year
annual_rets *= 100
annual_rets.iplot(kind='bar', legend={'orientation': 'h'}, yTitle='%')

In [62]:
levels.drop('Strategy relative to Aric-Benchmark', axis='columns').tearsheet(
    benchmark=env._load_benchmark().loc['2008':].squeeze(),
    risk_free=env._load_risk_free().loc['2008':].squeeze(),
    #weights=env.broker.track_record.to_frame('weights_target').iloc[1:]
)

Strategy  \
Context              From                              2008-01-01   
                     To                                2018-08-28   
                     Years                                 10.663   
                     Observations                            2771   
                     Risk-free asset        Index(USD 1M Deposit)   
                     Risk-free CAGR                    0.00736481   
Return               CAGR                                0.124306   
                     CAGR over cash                      0.116941   
                     Overall return                       2.48803   
Risk                 Volatility                          0.095085   
                     Downside volatility                0.0738826   
                     Upside volatility                  0.0651288   
                     Max drawdown                       -0.124261   
                     Martin risk                        0.0235286   
                     VaR 5%                           -0.00922837   
                     VaR 2%                            -0.0129208   
                     Expected shortfall 5%             -0.0137492   
                     Expected shortfall 2%             -0.0180508   
Risk-adjusted return Sharpe ratio                         1.22985   
                     Sortino ratio                        1.58279   
                     Calmar ratio                        0.941087   
                     Martin ratio                         4.97016   
Outperformance       Benchmark name         Index(Aric-Benchmark)   
                     CAGR over benchmark               -0.0353479   
                     Information ratio                   -0.56465   
                     CAPM Alpha                        0.00244577   
                     CAPM Beta                           0.768506   

                                            Index(Aric-Benchmark)  \
Context              From                              2008-01-01   
                     To                                2018-08-28   
                     Years                                 10.663   
                     Observations                            2771   
                     Risk-free asset        Index(USD 1M Deposit)   
                     Risk-free CAGR                    0.00736481   
Return               CAGR                                0.161394   
                     CAGR over cash                       0.15403   
                     Overall return                       3.93038   
Risk                 Volatility                         0.0974619   
                     Downside volatility                 0.070126   
                     Upside volatility                  0.0705954   
                     Max drawdown                      -0.0865477   
                     Martin risk                        0.0184664   
                     VaR 5%                           -0.00907706   
                     VaR 2%                             -0.013463   
                     Expected shortfall 5%             -0.0138517   
                     Expected shortfall 2%             -0.0178668   
Risk-adjusted return Sharpe ratio                         1.58041   
                     Sortino ratio                        2.19647   
                     Calmar ratio                         1.77971   
                     Martin ratio                         8.34109   
Outperformance       Benchmark name         Index(Aric-Benchmark)   
                     CAGR over benchmark               0.00174106   
                     Information ratio                   0.253024   
                     CAPM Alpha                        0.00214802   
                     CAPM Beta                           0.994949   

                                            Index(USD 1M Deposit)  \
Context              From                              2008-01-01   
                     To                              

In [63]:
mapping_functions

{2007:                 Target weight: ETF(Russell 1000, SMART, USD)
 GAIA Predictor                                              
 0.000000                                            0.198985
 0.000000                                            0.198985
 0.000000                                            0.198985
 0.000000                                            0.198985
 0.000000                                            0.198985
 0.000000                                            0.198985
 0.000000                                            0.198985
 1.688722                                            0.596809
 0.000000                                            0.355523
 0.000000                                            0.198985
 0.000000                                            0.198985
 0.000000                                            0.198985
 0.000000                                            0.198985
 0.000000                                            0.198985
 0

In [70]:
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
import cufflinks
cufflinks.go_offline()
init_notebook_mode(connected=False)


traces = list()
for year, series in mapping_functions.items():
    trace = go.Scatter(
        x = list(series.squeeze().index[:-1]),
        y = list(series.squeeze().values[:-1]),
        mode = 'markers',
        name = year
    )
    traces.append(trace)
    
layout = go.Layout(
    title='GAIA vs RL mapping functions',
    xaxis=dict(
        title='GAIA Mapping'
    ),
    yaxis=dict(
        title='PPO Mapping'
        )
        
    )
fig = go.Figure(data=traces,layout=layout)
iplot(fig,filename='scatter=mode')

# iplot(traces, filename='scatter-mode')

## Tensorboard

## Restore the agents

## Run and visualize the agents out-of-sample

# Solve GAIA-v7 with ray (walk-forward, transfer learning)
TODO: walk-forward re-training using a sliding (i.e. not expanding) window. An expanding window is bad because the agent would overweight old observations as they would be used more often than recent observations.